In [2]:
import os
import pytz
import math
import numpy as np
import pandas as pd
import datetime
from plotly.subplots import make_subplots
from azureml.core import Workspace, Dataset
import warnings
warnings.filterwarnings("ignore")

In [3]:
WORKDIR = os.getcwd()
MODEL_NAME = "baseline"

In [4]:
ws = Workspace.from_config()

In [5]:
ds = Dataset.get_by_name(ws, name="energy_data_15_min")
print(ds.name, ds.version)

energy_data_15_min 1


In [6]:
df = ds.to_pandas_dataframe()
df = df.set_index("data_index_")

In [7]:
df.head()

temperature  solar_ghi  solar_prediction_mw  \
data_index_                                                        
2020-01-01 00:00:00   274.989655        0.0                  0.0   
2020-01-01 00:15:00   274.925659        0.0                  0.0   
2020-01-01 00:30:00   274.861694        0.0                  0.0   
2020-01-01 00:45:00   274.797699        0.0                  0.0   
2020-01-01 01:00:00   274.423157        0.0                  0.0   

                     wind_prediction_mw  load_actuals_mw  
data_index_                                               
2020-01-01 00:00:00           70.865426        95.756328  
2020-01-01 00:15:00           69.296785        94.836196  
2020-01-01 00:30:00           66.977409        93.798127  
2020-01-01 00:45:00           64.305715        92.162902  
2020-01-01 01:00:00           61.128262        91.506670

## 1A. Baseline model

Because demand has a strong daily and weekly pattern, the baseline model is a seasonal naive forecats. The predicted demand is the demand at the same time of the day 1 week ago.

In [8]:
# Baseline model: Shifted by 1 week
df_load_baseline = df.copy(deep=True).reset_index()[["load_actuals_mw"]]

df_load_baseline["data_index_"] = pd.to_datetime(
  df.reset_index()["data_index_"]
) + datetime.timedelta(weeks=1)

df_load_baseline = df_load_baseline.set_index("data_index_").rename(
    columns={"load_actuals_mw": "baseline"}
)

In [9]:
def plot_figure_load(df):
    fig = go.Figure(
        make_subplots(
            shared_xaxes=True, vertical_spacing=0.02,
        )
    )
    fig.add_trace(
        go.Scatter(
            x=df.index,
            y=df["load_actuals_mw"],
            name="Actual",
            legendgroup="Actual",
            showlegend=True,
            line_color="green",
            opacity=0.5,
        ))
    title_text = "Energy demand"
    fig.update_layout(title={'text': title_text,
                             'y': 0.95,
                             'x': 0.5,
                             'xanchor': 'center',
                             'yanchor': 'top'},
                      autosize=False,
                      width=800,
                      height=800,
                      paper_bgcolor='white',
                      plot_bgcolor='white'
                      )

    fig.update_yaxes(title_text="Demand [MW]", title_standoff=30, title_font=dict(size=12),
                     showgrid=True, gridcolor='lightgrey',
                     zeroline=True, zerolinecolor='lightgrey',
                     )
    fig.update_xaxes(title_text="Date",
                     showgrid=True, gridcolor='lightgrey',
                     zeroline=True, zerolinecolor='lightgrey',
                     )

    return fig

In [11]:
# Plot next to each other
fig = plot_figure_load(df)

# Plot baseline prediction
fig.add_trace(
    go.Scatter(
        x=df_load_baseline.index,
        y=df_load_baseline["baseline"],
        name="Baseline model",
        legendgroup="Baseline model",
        showlegend=True,
        line_color="orange",
        opacity=0.5,
    ),
    col=1,
    row=1,
)

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

## 1B. ML model

In [43]:
# add seasonal features
df['hour'] = df.index.hour
df['quarter_of_day'] =  np.where(df['hour'] > 0, df['hour'].apply(lambda x: math.ceil(x / 6.)), 4)
df['quarter_of_year'] = df.index.quarter
df['day'] = df.index.day
df['day_of_week'] = df.index.dayofweek
df['month'] = df.index.month
df['year'] = df.index.year

In [44]:
# holiday indicator feature
from workalendar.europe import Netherlands
cal = Netherlands(include_carnival=True)

# Make a pandas series with holidays of interest
holidates = cal.holidays(2020) + cal.holidays(2021)
pd_holidays = pd.to_datetime([d[0] for d in holidates])

df['is_holiday'] = pd.to_datetime(df.index.date).isin(pd_holidays)

In [45]:
def add_fourier_features(df, column_name, period, n, period_name = "f"):
    t = df[column_name]
    for i in range(n):
        j = math.ceil((i+1)/2)
        if i%2:
            df[f'{period_name}_{i}'] = np.cos(j * 2 * np.pi * t / period)
        else:
            df[f'{period_name}_{i}'] = np.sin(j * 2 * np.pi * t / period)
    return df

In [46]:
def create_workday_weekend_features(df, fourier_order):
    # split features in workday / weekend
    df['is_workday'] = (~(df.is_holiday.astype(bool) | (df.day_of_week == 5) | (df.day_of_week == 6)))
    workday_data = {
        f'workday_{k}':df[k]*df.is_workday.astype(int)
        for k
        in ['temperature', 'solar_ghi'] + [f'f_quarter_{f}' for f in range(fourier_order)]
    }
    weekend_data = {
        f'weekend_{k}':df[k]*(~df.is_workday).astype(int)
        for k
        in ['temperature', 'solar_ghi'] + [f'f_quarter_{f}' for f in range(fourier_order)]
    }
    return workday_data, weekend_data

In [47]:
# add Fourier features to capture daily pattern in model
fourier_order = 6

df = add_fourier_features(df, "quarter_of_day", 4 * 24, fourier_order, "f_quarter")

In [48]:
df.head()

temperature  solar_ghi  solar_prediction_mw  \
data_index_                                                        
2020-01-01 00:00:00   274.989655        0.0                  0.0   
2020-01-01 00:15:00   274.925659        0.0                  0.0   
2020-01-01 00:30:00   274.861694        0.0                  0.0   
2020-01-01 00:45:00   274.797699        0.0                  0.0   
2020-01-01 01:00:00   274.423157        0.0                  0.0   

                     wind_prediction_mw  load_actuals_mw  hour  \
data_index_                                                      
2020-01-01 00:00:00           70.865426        95.756328     0   
2020-01-01 00:15:00           69.296785        94.836196     0   
2020-01-01 00:30:00           66.977409        93.798127     0   
2020-01-01 00:45:00           64.305715        92.162902     0   
2020-01-01 01:00:00           61.128262        91.506670     1   

                     quarter_of_day  quarter_of_year  day  day_of_week  month  \
data_index_                                                                     
2020-01-01 00:00:00               4                1    1            2      1   
2020-01-01 00:15:00               4                1    1            2      1   
2020-01-01 00:30:00               4                1    1            2      1   
2020-01-01 00:45:00               4                1    1            2      1   
2020-01-01 01:00:00               1                1    1            2      1   

                     year  f_quarter_0  f_quarter_1  f_quarter_2  f_quarter_3  \
data_index_                                                                     
2020-01-01 00:00:00  2020     0.258819     0.965926     0.500000     0.866025   
2020-01-01 00:15:00  2020     0.258819     0.965926     0.500000     0.866025   
2020-01-01 00:30:00  2020     0.258819     0.965926     0.500000     0.866025   
2020-01-01 00:45:00  2020     0.258819     0.965926     0.500000     0.866025   
2020-01-01 01:00:00  2020     0.065403     0.997859     0.130526     0.991445   

                     f_quarter_4  f_quarter_5  is_holiday  
data_index_                                                
2020-01-01 00:00:00     0.707107     0.707107        True  
2020-01-01 00:15:00     0.707107     0.707107        True  
2020-01-01 00:30:00     0.707107     0.707107        True  
2020-01-01 00:45:00     0.707107     0.707107        True  
2020-01-01 01:00:00     0.195090     0.980785        True

In [42]:
# split workdays and weekend/holidays
workday_data, weekend_data = create_workday_weekend_features(df, fourier_order)
df_linregr = pd.DataFrame(
    {**workday_data, **weekend_data, "load": df["load_actuals_mw"]}
)

AttributeError: 'DataFrame' object has no attribute 'is_holiday'

In [25]:
# List the input feature columns
feat_columns = list(workday_data.keys()) + list(weekend_data.keys())

In [26]:
# Define size of train and test set of model
number_of_training_days = 30
number_of_test_days = 30

test_start_date_run_i = df_linregr.index.min() + datetime.timedelta(
    days=number_of_training_days
)
test_end_date = df_linregr.index.max()
df_result = pd.DataFrame()

# Run model for full period of data set
while True:
    print(f"Start of prediction of this run: {test_start_date_run_i}")

    # split train/test set
    df_train = df_linregr[
        test_start_date_run_i
        - datetime.timedelta(days=number_of_training_days) : test_start_date_run_i
    ]

    df_test = df_linregr[
        test_start_date_run_i : test_start_date_run_i
        + datetime.timedelta(days=number_of_test_days)
    ]

    lr = LinearRegression()
    lr.fit(df_train[feat_columns], df_train["load"])
    
    y_pred = lr.predict(df_test[feat_columns])
    
    # Combine results
    df_result_run_i = pd.DataFrame(
        {
            "load": df_test["load"],
            "pred": y_pred,
        }
    )

    # Store results in a single dataframe
    df_result = df_result.append(df_result_run_i)
    # Adjust start date of test set for next run
    test_start_date_run_i = test_start_date_run_i + datetime.timedelta(
        days=number_of_test_days
    )
    if test_start_date_run_i > test_end_date:
        break 

Start of prediction of this run: 2020-01-31 00:00:00


<IPython.core.display.Javascript object>

Start of prediction of this run: 2020-03-01 00:00:00


<IPython.core.display.Javascript object>

ValueError: Found array with 0 sample(s) (shape=(0, 16)) while a minimum of 1 is required.